In [1]:
# Multi-level Stacking Regression

# Importing the libraries
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
from sklearn.linear_model import RidgeCV
from sklearn.svm import LinearSVR
from sklearn import linear_model
from sklearn.ensemble import StackingRegressor
from sklearn.ensemble import RandomForestRegressor
from sklearn.ensemble import GradientBoostingRegressor
from sklearn.neural_network import MLPRegressor
from sklearn.linear_model import LassoCV
from sklearn.svm import SVR
from sklearn.ensemble import ExtraTreesRegressor
from sklearn.ensemble import AdaBoostRegressor
from sklearn.tree import DecisionTreeRegressor
from sklearn.neighbors import KNeighborsRegressor
from sklearn.linear_model import SGDRegressor
from xgboost import XGBRegressor
from sklearn.metrics import mean_squared_error as mse

In [3]:
dataset = pd.read_csv('Total_combined_csv.csv')
dataset.head()

File  LOC  SLOC_P  SLOC_L  \
0  org.eclipse.jdt.core/antadapter/org/eclipse/jd...  231     108      89   
1  org.eclipse.jdt.core/batch/org/eclipse/jdt/int...  117      93      71   
2  org.eclipse.jdt.core/batch/org/eclipse/jdt/int...   78      57      46   
3  org.eclipse.jdt.core/batch/org/eclipse/jdt/int...   74      53      38   
4  org.eclipse.jdt.core/batch/org/eclipse/jdt/int...   49      36      26   

   MVG  BLOC  C_SLOC  CLOC  CWORD  HCLOC  ...  NSUP  TCC  NSUB  MPC  NCO  \
0   17    26      24    97    419     10  ...     1   20     0    0    2   
1   29    12      11    12    126     10  ...     0   28     0    0    5   
2   10     9       4    12     86     10  ...     0   15     0    0    4   
3   13     9       5    12     76     10  ...     0   13     0    0    5   
4    8     3       1    10     60     10  ...     0   10     0    0    2   

   INTR  CCOM  HLTH  MOD  bug_cnt  
0     0    46   594    1        3  
1     1    13   599    1        0  
2     1     6   282    1        0  
3     1    10   270    1        2  
4     0     1   236    1        0  

[5 rows x 50 columns]

In [4]:
X = dataset.iloc[:,1 :-1].values
y = dataset.iloc[:, -1].values
# Splitting the dataset into the Training set and Test set
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size = 0.20, random_state = 0)
# Feature Scaling
from sklearn.preprocessing import StandardScaler
sc = StandardScaler()
X_train = sc.fit_transform(X_train)
X_test = sc.transform(X_test)
y_train= y_train.reshape(-1, 1)
y_test= y_test.reshape(-1, 1)
sc.fit(y_train)
y_train = sc.transform(y_train)
#y_test = sc.transform(y_test)

In [5]:
from sklearn.experimental import enable_hist_gradient_boosting 
from sklearn.ensemble import HistGradientBoostingRegressor
final_layer = StackingRegressor(
     estimators=[  ('xgbr', XGBRegressor(criterion= 'gini', max_depth= 20, max_features= 'auto', min_samples_leaf= 0, n_estimators= 10)), 
                 ('sgdr', SGDRegressor(max_iter=3000, tol=1e-3)), 
                 ('dtr', DecisionTreeRegressor(random_state=42)),
                 ('adbr', AdaBoostRegressor(random_state=42, n_estimators=100)),
                 ('gbrt', HistGradientBoostingRegressor(random_state=42)),
                 ('rf', RandomForestRegressor(random_state=42)),
                 ('etr', ExtraTreesRegressor(n_estimators=100, max_depth=5, max_features=0.5, random_state=42))
                 ],
     final_estimator= RidgeCV(), passthrough=True, n_jobs=-1
    #MLPRegressor(hidden_layer_sizes = (250,700,102,51),max_iter=3500, activation = 'relu', solver = 'adam', alpha = 0.01, random_state = 1)
    )
multi_layer_regressor = StackingRegressor(
        estimators=[ 
                 
                 ('lr', RidgeCV()),
                 ('lasso', LassoCV(random_state=42)),  
                 ('lrr',linear_model.LinearRegression()),
                 ('nn', MLPRegressor(hidden_layer_sizes = (250,700,102,51),max_iter=3500, activation = 'relu', solver = 'adam', alpha = 0.01, random_state = 42)),
                 ('svr', SVR(C=1, gamma=1e-6, kernel='rbf'))],
         final_estimator=final_layer, passthrough=False, n_jobs=-1
   )
multi_layer_regressor.fit(X_train, y_train)

#print('R2 score: {:.2f}'          .format(multi_layer_regressor.score(X_test, y_test)))
y_pred = multi_layer_regressor.predict(X_test)
# y_pred=sc.inverse_transform(y_pred) #inverse transform of y_pred to de-normalized values
#mse(y_test, y_pred)
from sklearn.metrics import r2_score
print(f"Mean Squared Error is {mse(y_test,y_pred)}")
print(f"R2 Score is {r2_score(y_test,y_pred)}")
#r2_score(y_test,y_pred)

/opt/conda/lib/python3.7/site-packages/sklearn/experimental/enable_hist_gradient_boosting.py:17: UserWarning: Since version 1.0, it is not needed to import enable_hist_gradient_boosting anymore. HistGradientBoostingClassifier and HistGradientBoostingRegressor are now stable and can be normally imported from sklearn.ensemble.
  "Since version 1.0, "
/opt/conda/lib/python3.7/site-packages/sklearn/ensemble/_stacking.py:758: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
/opt/conda/lib/python3.7/site-packages/sklearn/linear_model/_coordinate_descent.py:644: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 3.911796948364099, tolerance: 1.3337127326716278
  positive,
/opt/conda/lib/python3.7/site-packages/sklearn/linear_model/_coordinate_descent.py:644: ConvergenceWarning: Objective did n

Mean Squared Error is 6.058805648728522
R2 Score is 0.08552373978232308


In [6]:
# Applying k-Fold Cross Validation
"""from sklearn.model_selection import cross_val_score
score = cross_val_score(estimator = multi_layer_regressor, X = X_train, y = y_train, cv = 5, scoring='neg_mean_squared_error')
print(score)
print("Error: {:.2f} ".format(score.mean()))
print("Standard Deviation: {:.2f} %".format(score.std()*100)) """

'from sklearn.model_selection import cross_val_score\nscore = cross_val_score(estimator = multi_layer_regressor, X = X_train, y = y_train, cv = 5, scoring=\'neg_mean_squared_error\')\nprint(score)\nprint("Error: {:.2f} ".format(score.mean()))\nprint("Standard Deviation: {:.2f} %".format(score.std()*100)) '

In [7]:
# Applying k-Fold Cross Validation using Shuffle Split
from sklearn.model_selection import ShuffleSplit
from sklearn.model_selection import cross_val_score
n_samples = X_train.shape[0]
cv = ShuffleSplit(n_splits=5, test_size=0.20, random_state=0)
score=cross_val_score(multi_layer_regressor, X_train, y_train, cv=cv,scoring='neg_mean_squared_error', n_jobs=-1)
print(score)
print("Error: {:.2f} ".format(score.mean()))
print("Standard Deviation: {:.2f} %".format(score.std()*100))

/opt/conda/lib/python3.7/site-packages/sklearn/ensemble/_stacking.py:758: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
/opt/conda/lib/python3.7/site-packages/sklearn/linear_model/_coordinate_descent.py:644: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 2.024847738871358, tolerance: 1.0058838145084021
  positive,
/opt/conda/lib/python3.7/site-packages/sklearn/linear_model/_coordinate_descent.py:644: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 4.338172361908619, tolerance: 1.0058838145084021
  positive,
/opt/conda/lib/python3.7/site-packages/sklearn/linear_model/_coordinate_descent.py:644: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 4.7249363

[05:46:22] WARNING: ../src/learner.cc:627: 
Parameters: { "criterion", "max_features", "min_samples_leaf" } might not be used.

  This could be a false alarm, with some parameters getting used by language bindings but
  then being mistakenly passed down to XGBoost core, or some parameter actually being used
  but getting flagged wrongly here. Please open an issue if you find any such cases.




/opt/conda/lib/python3.7/site-packages/sklearn/linear_model/_coordinate_descent.py:644: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 2.2002179619375966, tolerance: 0.855435627049607
  positive,
/opt/conda/lib/python3.7/site-packages/sklearn/linear_model/_coordinate_descent.py:644: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 2.4057111431475278, tolerance: 0.855435627049607
  positive,
/opt/conda/lib/python3.7/site-packages/sklearn/linear_model/_coordinate_descent.py:644: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 2.4306937551482406, tolerance: 0.855435627049607
  positive,
/opt/conda/lib/python3.7/site-packages/sklearn/linear_model/_coordinate_descent.py:644: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 2.3442887

[-0.47051126 -0.46145647 -0.6422109  -0.60823393 -0.74196442]
Error: -0.58 
Standard Deviation: 10.66 %


In [8]:
from sklearn.model_selection import RandomizedSearchCV
from time import time
# specify parameters and distributions to sample from
"""param_dist = {'average': [True, False],
              'l1_ratio': stats.uniform(0, 1),
              'alpha': loguniform(1e-4, 1e0)}"""
params = {
             'final_estimator__xgbr__max_depth': [20, 23, 25],  
                'final_estimator__etr__max_features': [0.5 , 1], 'final_estimator__etr__max_depth': [5 , 10, 20],
             'final_estimator__adbr__n_estimators':[100, 200], 'svr__gamma': ['scale', 'auto', 1e-6]
             }

# run randomized search
n_iter_search = 15
random_search = RandomizedSearchCV(multi_layer_regressor, param_distributions=params,cv=cv,
                                   n_iter=n_iter_search, n_jobs=-1)

start = time()
random_search.fit(X_train, y_train)
print("RandomizedSearchCV took %.2f seconds for %d candidates"
      " parameter settings." % ((time() - start), n_iter_search))
#report(random_search.cv_results_)

/opt/conda/lib/python3.7/site-packages/sklearn/linear_model/_coordinate_descent.py:644: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 6.554257521198451, tolerance: 0.8101448857865107
  positive,
/opt/conda/lib/python3.7/site-packages/sklearn/linear_model/_coordinate_descent.py:644: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 2.082500067484034, tolerance: 0.7119686282852015
  positive,
/opt/conda/lib/python3.7/site-packages/sklearn/linear_model/_coordinate_descent.py:644: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 2.4240681104120085, tolerance: 0.7119686282852015
  positive,
/opt/conda/lib/python3.7/site-packages/sklearn/linear_model/_coordinate_descent.py:644: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 2.458433

RandomizedSearchCV took 21642.79 seconds for 15 candidates parameter settings.


In [9]:
#multi_layer_regressor.get_params().keys()
from sklearn.metrics import explained_variance_score
from sklearn.metrics import max_error, mean_absolute_error, median_absolute_error, mean_squared_log_error

In [10]:
#Random Search Model
# Predicting the Test set results
#y_pred = multi_layer_regressor.predict(X_test)
best_error = random_search.best_score_
best_parameters = random_search.best_params_
print("Best Error: {:.2f} %".format(best_error*100))
print("Best Parameters:", best_parameters)

y_pred_restored = random_search.predict(X_test)
# y_pred_restored=sc.inverse_transform(y_pred)
#y_test_restored=sc.inverse_transform(y_test)
print(f"Mean Squared Error is {mse(y_test,y_pred_restored)}")
print(f"R2 Score is {r2_score(y_test,y_pred_restored)}")
print(f"Expained Variance Score is {explained_variance_score(y_test,y_pred_restored)}")
print(f"Maximum Error is {max_error(y_test,y_pred_restored)}")
print(f"Mean Absolute Error is {mean_absolute_error(y_test,y_pred_restored)}")
print(f"median_absolute_error is {median_absolute_error(y_test,y_pred_restored)}")

Best Error: 44.12 %
Best Parameters: {'svr__gamma': 'scale', 'final_estimator__xgbr__max_depth': 20, 'final_estimator__etr__max_features': 0.5, 'final_estimator__etr__max_depth': 10, 'final_estimator__adbr__n_estimators': 200}
Mean Squared Error is 5.937074223164016
R2 Score is 0.10389708021527733
Expained Variance Score is 0.2664114135899994
Maximum Error is 32.02485619821775
Mean Absolute Error is 1.0937508061266175
median_absolute_error is 0.28812603407943743


In [11]:
#Original Model
y_pred0_restored = multi_layer_regressor.predict(X_test)
# y_pred0_restored=sc.inverse_transform(y_pred0) #inverse transform of y_pred to de-normalized values
#mse(y_test, y_pred)
from sklearn.metrics import r2_score
print(f"Mean Squared Error is {mse(y_test,y_pred0_restored)}")
print(f"R2 Score is {r2_score(y_test,y_pred0)}")
print(f"Expained Variance Score is {explained_variance_score(y_test,y_pred0_restored)}")
print(f"Maximum Error is {max_error(y_test,y_pred0_restored)}")
print(f"Mean Absolute Error is {mean_absolute_error(y_test,y_pred0_restored)}")
print(f"median_absolute_error is {median_absolute_error(y_test,y_pred0_restored)}")

Mean Squared Error is 6.058805648728522


NameError: name 'y_pred0' is not defined

In [ ]:
# Modified Model
final_layer1 = StackingRegressor(
     estimators=[  ('xgbr', XGBRegressor(criterion= 'gini', max_depth= 25, max_features= 'auto', min_samples_leaf= 0, n_estimators= 10)), 
                 ('sgdr', SGDRegressor(max_iter=3000, tol=1e-3)), 
                 ('dtr', DecisionTreeRegressor(random_state=42)),
                 ('adbr', AdaBoostRegressor(random_state=42, n_estimators=100)),
                 ('gbrt', HistGradientBoostingRegressor(random_state=42)),
                 ('rf', RandomForestRegressor(random_state=42)),
                 ('etr', ExtraTreesRegressor(n_estimators=100, max_depth=10, max_features=0.5, random_state=42))
                 ],
     final_estimator= RidgeCV(), passthrough=True, n_jobs=-1
    #MLPRegressor(hidden_layer_sizes = (250,700,102,51),max_iter=3500, activation = 'relu', solver = 'adam', alpha = 0.01, random_state = 1)
    )
multi_layer_regressor1 = StackingRegressor(
        estimators=[ 
                 
                 ('lr', RidgeCV()),
                 ('lasso', LassoCV(random_state=42)),  
                 ('lrr',linear_model.LinearRegression()),
                 ('nn', MLPRegressor(hidden_layer_sizes = (250,700,102,51),max_iter=3500, activation = 'relu', solver = 'adam', alpha = 0.01, random_state = 42)),
                 ('svr', SVR(C=1, gamma='auto', kernel='rbf'))],
         final_estimator=final_layer1, passthrough=False, n_jobs=-1
   )
multi_layer_regressor1.fit(X_train, y_train)

In [ ]:
# Modified Model
y_pred1_restored = multi_layer_regressor1.predict(X_test)
# y_pred1_restored=sc.inverse_transform(y_pred1)
print(f"Mean Squared Error is {mse(y_test,y_pred1_restored)}")
print(f"R2 Score is {r2_score(y_test,y_pred1_restored)}")
print(f"Expained Variance Score is {explained_variance_score(y_test,y_pred1_restored)}")
print(f"Maximum Error is {max_error(y_test,y_pred1_restored)}")
print(f"Mean Absolute Error is {mean_absolute_error(y_test,y_pred1_restored)}")
print(f"median_absolute_error is {median_absolute_error(y_test,y_pred1_restored)}")

In [ ]:
# Modified Model1
final_layer1 = StackingRegressor(
     estimators=[  ('xgbr', XGBRegressor(criterion= 'gini', max_depth= 20, max_features= 'auto', min_samples_leaf= 0, n_estimators= 10)), 
                 ('sgdr', SGDRegressor(max_iter=3000, tol=1e-3)), 
                 ('dtr', DecisionTreeRegressor(random_state=42)),
                 ('adbr', AdaBoostRegressor(random_state=42, n_estimators=100)),
                 ('gbrt', HistGradientBoostingRegressor(random_state=42)),
                 ('rf', RandomForestRegressor(random_state=42)),
                 ('etr', ExtraTreesRegressor(n_estimators=100, max_depth=5, max_features=0.5, random_state=42))
                 ],
     final_estimator= RidgeCV(), passthrough=True, n_jobs=-1
    #MLPRegressor(hidden_layer_sizes = (250,700,102,51),max_iter=3500, activation = 'relu', solver = 'adam', alpha = 0.01, random_state = 1)
    )
multi_layer_regressor2 = StackingRegressor(
        estimators=[ 
                 
                 ('lr', RidgeCV()),
                 ('lasso', LassoCV(random_state=42)),  
                 ('lrr',linear_model.LinearRegression()),
                 ('nn', MLPRegressor(hidden_layer_sizes = (250,700,102,51),max_iter=3500, activation = 'relu', solver = 'adam', alpha = 0.01, random_state = 42)),
                 ('svr', SVR(C=1, gamma='auto', kernel='rbf'))],
         final_estimator=final_layer1, passthrough=False, n_jobs=-1
   )
multi_layer_regressor2.fit(X_train, y_train)

In [ ]:
# Modified Model1
y_pred1_restored = multi_layer_regressor2.predict(X_test)
# y_pred1_restored=sc.inverse_transform(y_pred1)
print(f"Mean Squared Error is {mse(y_test,y_pred1_restored)}")
print(f"R2 Score is {r2_score(y_test,y_pred1_restored)}")
print(f"Expained Variance Score is {explained_variance_score(y_test,y_pred1_restored)}")
print(f"Maximum Error is {max_error(y_test,y_pred1_restored)}")
print(f"Mean Absolute Error is {mean_absolute_error(y_test,y_pred1_restored)}")
print(f"median_absolute_error is {median_absolute_error(y_test,y_pred1_restored)}")